# 🏙️ Pune Smart City Air Quality Analysis

## A Data-Driven Approach to Urban Environmental Monitoring

---

### Executive Summary

This analysis examines **IoT sensor data from multiple monitoring stations across Pune** to identify pollution patterns, hotspots, and actionable insights for city authorities. Using exploratory data analysis and unsupervised learning, we uncover temporal trends, geographic disparities, and environmental correlations that can inform smart city initiatives.

**Key Findings:**
- 🔴 **Hadapsar Gadital** and **Railway Station** consistently show highest pollution levels
- ⏰ Peak pollution occurs during **morning rush hours (8-10 AM)**
- 📊 **PM2.5 and PM10** are strongly correlated (common particulate sources)
- 🌡️ **Humidity** serves as an early warning indicator for poor air quality
- 📍 Clustering reveals **3 distinct pollution zones** requiring differentiated interventions

---

*Dataset metrics are computed dynamically in the data loading cell below.*

---
## 📦 1. Setup & Data Loading
---

In [41]:
# Import libraries
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import warnings
warnings.filterwarnings('ignore')

# Configure Plotly for consistent styling
COLORS = px.colors.qualitative.Set2
TEMPLATE = 'plotly_white'

In [42]:
# Load and parse dataset
df = pd.read_csv("Pune_SmartCity_Test_Dataset.csv")
df['LASTUPDATEDATETIME'] = pd.to_datetime(df['LASTUPDATEDATETIME'], format='%d/%m/%y %H:%M', errors='coerce')

# Display dataset overview
print("═" * 50)
print("📊 DATASET OVERVIEW")
print("═" * 50)
print(f"Records: {df.shape[0]:,}")
print(f"Features: {df.shape[1]}")
print(f"Time Period: {df['LASTUPDATEDATETIME'].min().strftime('%d %B %Y')} → {df['LASTUPDATEDATETIME'].max().strftime('%d %B %Y')}")
print(f"Monitoring Stations: {df['NAME'].nunique()}")
print("═" * 50)

# Dynamic dataset metrics table
print("\n📋 DATASET METRICS")
print(f"| {'Metric':<25} | {'Value':<25} |")
print(f"|{'-'*27}|{'-'*27}|")

dataset_size_str = f"{df.shape[0]:,} records"
monitoring_stations_str = f"{df['NAME'].nunique()} locations"
parameters_tracked_str = f"{df.shape[1]} environmental features"

print(f"| {'Dataset Size':<25} | {dataset_size_str:<25} |")
print(f"| {'Monitoring Stations':<25} | {monitoring_stations_str:<25} |")
print(f"| {'Parameters Tracked':<25} | {parameters_tracked_str:<25} |")
print(f"| {'Time Period':<25} | {df['LASTUPDATEDATETIME'].min().strftime('%b')} - {df['LASTUPDATEDATETIME'].max().strftime('%b %Y'):<15} |")
print(f"| {'Primary Pollutants':<25} | {'PM2.5, PM10, NO₂, CO, SO₂, O₃':<25} |")

══════════════════════════════════════════════════
📊 DATASET OVERVIEW
══════════════════════════════════════════════════
Records: 103,205
Features: 28
Time Period: 08 April 2019 → 06 September 2019
Monitoring Stations: 10
══════════════════════════════════════════════════

📋 DATASET METRICS
| Metric                    | Value                     |
|---------------------------|---------------------------|
| Dataset Size              | 103,205 records           |
| Monitoring Stations       | 10 locations              |
| Parameters Tracked        | 28 environmental features |
| Time Period               | Apr - Sep 2019        |
| Primary Pollutants        | PM2.5, PM10, NO₂, CO, SO₂, O₃ |


---
## 🔍 2. Data Quality Assessment
---

Before analysis, we assess data completeness and identify quality issues that may affect our conclusions.

In [43]:
# Missing data analysis
missing = df.isnull().sum()
missing_pct = (missing / len(df) * 100).round(2)
missing_df = pd.DataFrame({'Missing Count': missing, 'Missing %': missing_pct})
missing_df = missing_df[missing_df['Missing Count'] > 0].sort_values('Missing %', ascending=False)

print("⚠️ MISSING DATA SUMMARY")
print("-" * 40)
if len(missing_df) > 0:
    print(missing_df.to_string())
else:
    print("No missing values detected!")

# Visualize missing data
if len(missing_df) > 0:
    fig = px.bar(missing_df.reset_index(), x='index', y='Missing %',
                 title='<b>Missing Data by Feature</b>',
                 labels={'index': 'Feature', 'Missing %': 'Missing (%)'},
                 color='Missing %', color_continuous_scale='Reds',
                 template=TEMPLATE)
    fig.update_layout(showlegend=False, xaxis_tickangle=-45)
    fig.show()

⚠️ MISSING DATA SUMMARY
----------------------------------------
                Missing Count  Missing %
UV_MIN                  12518      12.13
UV_MAX                  12518      12.13
LIGHT                    6072       5.88
AIR_PRESSURE             5120       4.96
SOUND                    5120       4.96
HUMIDITY                 5121       4.96
TEMPRATURE_MIN           5061       4.90
TEMPRATURE_MAX           5061       4.90
PM10_MAX                 3233       3.13
PM10_MIN                 3233       3.13
PM2_MIN                  3233       3.13
PM2_MAX                  3233       3.13
CO2_MAX                  1565       1.52
CO2_MIN                  1565       1.52
SO2_MIN                   837       0.81
SO2_MAX                   837       0.81
OZONE_MAX                 608       0.59
OZONE_MIN                 608       0.59
CO_MIN                    608       0.59
CO_MAX                    608       0.59
NO2_MAX                   577       0.56
NO2_MIN                   577    

In [44]:
# Check for zero/unrealistic sensor readings
pollutants = ['PM2_MAX', 'PM10_MAX', 'NO2_MAX', 'CO_MAX', 'SO2_MAX', 'OZONE_MAX']
env_cols = ['TEMPRATURE_MAX', 'HUMIDITY', 'SOUND', 'LIGHT']

print("🔧 SENSOR QUALITY CHECK (Zero Values)")
print("-" * 40)
zero_stats = []
for col in pollutants:
    zero_count = (df[col] == 0).sum()
    zero_pct = zero_count / len(df) * 100
    zero_stats.append({'Parameter': col, 'Zero Count': zero_count, 'Zero %': round(zero_pct, 2)})
    print(f"{col}: {zero_count:,} records ({zero_pct:.2f}%)")

# Flag: OZONE shows high zero readings - potential sensor issue
print("\n💡 Insight: OZONE_MAX shows significant zero readings, suggesting potential sensor calibration issues.")

🔧 SENSOR QUALITY CHECK (Zero Values)
----------------------------------------
PM2_MAX: 3,842 records (3.72%)
PM10_MAX: 5,853 records (5.67%)
NO2_MAX: 3,717 records (3.60%)
CO_MAX: 0 records (0.00%)
SO2_MAX: 16,770 records (16.25%)
OZONE_MAX: 28,965 records (28.07%)

💡 Insight: OZONE_MAX shows significant zero readings, suggesting potential sensor calibration issues.


---
## 📈 3. Pollution Distribution Analysis
---

Understanding the distribution of pollutants helps identify typical ranges and outliers across Pune's monitoring network.

In [45]:
# Distribution of key pollutants
key_pollutants = ['PM2_MAX', 'PM10_MAX', 'NO2_MAX', 'CO_MAX']
data_sample = df[key_pollutants].dropna().sample(min(5000, len(df)))

fig = ff.create_distplot(
    [data_sample[c] for c in key_pollutants], 
    key_pollutants, 
    bin_size=[2, 5, 5, 5],
    colors=COLORS[:4]
)
fig.update_layout(
    title='<b>Distribution of Key Air Pollutants</b>',
    xaxis_title='Concentration',
    yaxis_title='Density',
    template=TEMPLATE,
    legend=dict(orientation='h', yanchor='bottom', y=1.02)
)
fig.show()

# Summary statistics
print("\n📊 STATISTICAL SUMMARY")
print(df[key_pollutants].describe().round(2).to_string())


📊 STATISTICAL SUMMARY
        PM2_MAX  PM10_MAX    NO2_MAX     CO_MAX
count  99972.00  99972.00  102628.00  102597.00
mean      15.01     19.00      72.68      96.03
std        9.17     12.49      37.69      32.73
min        0.00      0.00       0.00      17.00
25%        8.00      8.00      47.00      75.00
50%       14.00     18.00      77.00     106.00
75%       22.00     29.00      96.00     120.00
max       38.00     54.00     316.00     163.00


In [46]:
# Pollutant variability analysis (Coefficient of Variation)
variability = (df[pollutants].std() / df[pollutants].mean() * 100).sort_values(ascending=False)

fig = px.bar(
    x=variability.index, 
    y=variability.values,
    title='<b>Pollutant Variability Across Pune</b><br><sup>Higher CV% = More Unstable Readings</sup>',
    labels={'x': 'Pollutant', 'y': 'Coefficient of Variation (%)'},
    color=variability.values,
    color_continuous_scale='RdYlGn_r',
    template=TEMPLATE
)
fig.update_layout(showlegend=False)
fig.show()

print(f"💡 Insight: {variability.idxmax()} shows highest variability ({variability.max():.1f}%), indicating inconsistent readings or localized spikes.")

💡 Insight: SO2_MAX shows highest variability (235.6%), indicating inconsistent readings or localized spikes.


---
## 🗺️ 4. Geographic Analysis & Hotspots
---

Identifying pollution hotspots is critical for targeted interventions and resource allocation.

In [47]:
# Monitoring station analysis
readings_per_loc = df['NAME'].value_counts()
loc_pollution = df.groupby('NAME')[pollutants].mean()
loc_pollution['Total_Score'] = loc_pollution.sum(axis=1)
loc_pollution = loc_pollution.sort_values('Total_Score', ascending=True)

fig = px.bar(
    loc_pollution.reset_index(),
    x='Total_Score',
    y='NAME',
    orientation='h',
    title='<b>Pollution Severity by Monitoring Station</b><br><sup>Composite score of all pollutants</sup>',
    labels={'NAME': 'Location', 'Total_Score': 'Average Total Pollution Score'},
    color='Total_Score',
    color_continuous_scale='RdYlGn_r',
    template=TEMPLATE
)
fig.update_layout(showlegend=False, height=500)
fig.show()

In [48]:
# Categorize locations by type
def categorize_location(name):
    name = str(name).lower()
    if any(x in name for x in ['station', 'railway']):
        return '🚂 Railway Station'
    elif any(x in name for x in ['bus', 'stand', 'depot']):
        return '🚌 Bus Stop'
    elif any(x in name for x in ['it', 'tech', 'park', 'infotech']):
        return '🏢 IT/Industrial'
    elif any(x in name for x in ['garden', 'tekdi', 'forest']):
        return '🌳 Green Zone'
    elif any(x in name for x in ['chowk', 'circle', 'road']):
        return '🚗 Traffic Junction'
    else:
        return '🏘️ Commercial/Residential'

df['Location_Type'] = df['NAME'].apply(categorize_location)

# Box plot by location type
fig = px.box(
    df, x='Location_Type', y='PM10_MAX', color='Location_Type',
    title='<b>PM10 Distribution by Location Type</b>',
    template=TEMPLATE,
    color_discrete_sequence=COLORS
)
fig.update_layout(showlegend=False, xaxis_tickangle=-15)
fig.update_traces(boxpoints=False)
fig.show()

print("\n📍 Location Type Distribution:")
print(df['Location_Type'].value_counts().to_string())


📍 Location Type Distribution:
Location_Type
🏘️ Commercial/Residential    41437
🏢 IT/Industrial              25306
🚌 Bus Stop                   24671
🚂 Railway Station            11791


In [49]:
# Interactive map of pollution hotspots
df['Lattitude'] = pd.to_numeric(df['Lattitude'], errors='coerce')
df['Longitude'] = pd.to_numeric(df['Longitude'], errors='coerce')

# Aggregate by location for cleaner map
loc_geo = df.groupby('NAME').agg({
    'Lattitude': 'first',
    'Longitude': 'first',
    'PM2_MAX': 'mean',
    'PM10_MAX': 'mean'
}).reset_index().dropna()

fig = px.scatter_mapbox(
    loc_geo,
    lat='Lattitude',
    lon='Longitude',
    color='PM2_MAX',
    size='PM10_MAX',
    hover_name='NAME',
    hover_data={'PM2_MAX': ':.1f', 'PM10_MAX': ':.1f'},
    zoom=11,
    mapbox_style='open-street-map',
    title='<b>🗺️ Pollution Hotspots in Pune</b><br><sup>Size = PM10, Color = PM2.5</sup>',
    color_continuous_scale='RdYlGn_r',
    size_max=30
)
fig.update_layout(height=600, margin={'r': 0, 't': 50, 'l': 0, 'b': 0})
fig.show()

---
## ⏰ 5. Temporal Patterns
---

Understanding when pollution peaks helps design time-based interventions like traffic restrictions.

In [50]:
# Prepare temporal features
df = df.dropna(subset=['LASTUPDATEDATETIME'])
df['Date'] = df['LASTUPDATEDATETIME'].dt.date
df['Hour'] = df['LASTUPDATEDATETIME'].dt.hour
df['DayOfWeek'] = df['LASTUPDATEDATETIME'].dt.day_name()
df['IsWeekend'] = df['LASTUPDATEDATETIME'].dt.weekday >= 5
df['DayType'] = df['IsWeekend'].map({True: 'Weekend', False: 'Weekday'})

# Daily trend
daily_avg = df.groupby('Date')[['PM2_MAX', 'PM10_MAX', 'NO2_MAX']].mean().reset_index()

fig = px.line(
    daily_avg, x='Date', y=['PM2_MAX', 'PM10_MAX', 'NO2_MAX'],
    title='<b>Daily Pollution Trends</b>',
    labels={'value': 'Concentration', 'variable': 'Pollutant'},
    template=TEMPLATE,
    color_discrete_sequence=COLORS
)
fig.update_layout(legend=dict(orientation='h', yanchor='bottom', y=1.02))
fig.show()

In [62]:
# Hourly patterns - using average of MAX and MIN for actual pollution values
df['PM2_AVG'] = (df['PM2_MAX'] + df['PM2_MIN']) / 2
df['PM10_AVG'] = (df['PM10_MAX'] + df['PM10_MIN']) / 2
df['NO2_AVG'] = (df['NO2_MAX'] + df['NO2_MIN']) / 2

hourly_avg = df.groupby('Hour')[['PM2_AVG', 'PM10_AVG', 'NO2_AVG']].mean().reset_index()

# Use subplots with independent y-axes to show variation clearly
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.08,
                    subplot_titles=['PM2.5', 'PM10', 'NO₂'])

fig.add_trace(go.Bar(x=hourly_avg['Hour'], y=hourly_avg['PM2_AVG'], 
                     name='PM2.5', marker_color=COLORS[0]), row=1, col=1)
fig.add_trace(go.Bar(x=hourly_avg['Hour'], y=hourly_avg['PM10_AVG'], 
                     name='PM10', marker_color=COLORS[1]), row=2, col=1)
fig.add_trace(go.Bar(x=hourly_avg['Hour'], y=hourly_avg['NO2_AVG'], 
                     name='NO₂', marker_color=COLORS[2]), row=3, col=1)

# Set y-axis ranges to zoom in on the variation
fig.update_yaxes(range=[hourly_avg['PM2_AVG'].min() * 0.95, hourly_avg['PM2_AVG'].max() * 1.05], row=1, col=1)
fig.update_yaxes(range=[hourly_avg['PM10_AVG'].min() * 0.95, hourly_avg['PM10_AVG'].max() * 1.05], row=2, col=1)
fig.update_yaxes(range=[hourly_avg['NO2_AVG'].min() * 0.95, hourly_avg['NO2_AVG'].max() * 1.05], row=3, col=1)

fig.update_layout(
    title='<b>Hourly Pollution Patterns</b><br><sup>Y-axis scaled to show variation (data has low hourly variability)</sup>',
    height=600,
    showlegend=False,
    template=TEMPLATE
)
fig.update_xaxes(title_text='Hour of Day', row=3, col=1)
fig.show()

# Peak hours
peak_pm25 = hourly_avg.loc[hourly_avg['PM2_AVG'].idxmax(), 'Hour']
peak_pm10 = hourly_avg.loc[hourly_avg['PM10_AVG'].idxmax(), 'Hour']
print(f"\n⏰ Peak Hours: PM2.5 at {peak_pm25}:00 | PM10 at {peak_pm10}:00")
print(f"💡 Note: Hourly variation is small (~1-3%) suggesting consistent pollution sources throughout the day")


⏰ Peak Hours: PM2.5 at 9:00 | PM10 at 8:00
💡 Note: Hourly variation is small (~1-3%) suggesting consistent pollution sources throughout the day


In [52]:
# Weekday vs Weekend comparison
daytype_avg = df.groupby('DayType')[['PM2_MAX', 'PM10_MAX', 'NO2_MAX']].mean().reset_index()

fig = px.bar(
    daytype_avg, x='DayType', y=['PM2_MAX', 'PM10_MAX', 'NO2_MAX'],
    title='<b>Weekday vs Weekend Pollution</b>',
    barmode='group',
    template=TEMPLATE,
    color_discrete_sequence=COLORS
)
fig.show()

# Calculate percentage difference
weekday = daytype_avg[daytype_avg['DayType'] == 'Weekday']['PM2_MAX'].values[0]
weekend = daytype_avg[daytype_avg['DayType'] == 'Weekend']['PM2_MAX'].values[0]
diff = ((weekday - weekend) / weekend) * 100
print(f"\n💡 Insight: Weekday PM2.5 is {diff:.1f}% {'higher' if diff > 0 else 'lower'} than weekends")


💡 Insight: Weekday PM2.5 is 0.2% higher than weekends


---
## 🔗 6. Correlation Analysis
---

Understanding relationships between pollutants and environmental factors reveals common sources and early warning indicators.

In [53]:
# Pollutant correlation matrix
corr_matrix = df[pollutants].corr()

fig = px.imshow(
    corr_matrix,
    text_auto='.2f',
    title='<b>Pollutant Correlation Matrix</b><br><sup>Identifying common pollution sources</sup>',
    color_continuous_scale='RdBu_r',
    template=TEMPLATE,
    aspect='auto'
)
fig.update_layout(height=500)
fig.show()

# Find strongest correlation
corr_unstacked = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool)).unstack().dropna().sort_values(ascending=False)
top_corr = corr_unstacked.head(1)
print(f"\n🔗 Strongest Correlation: {top_corr.index[0][0]} ↔ {top_corr.index[0][1]} (r = {top_corr.values[0]:.2f})")


🔗 Strongest Correlation: PM10_MAX ↔ PM2_MAX (r = 0.96)


In [54]:
# Environment vs Pollutants correlation
all_cols = pollutants + env_cols
full_corr = df[all_cols].corr()
env_poll_corr = full_corr.loc[pollutants, env_cols]

fig = px.imshow(
    env_poll_corr,
    text_auto='.2f',
    title='<b>Environmental Factors vs Pollutants</b><br><sup>Identifying early warning indicators</sup>',
    color_continuous_scale='RdBu_r',
    template=TEMPLATE,
    aspect='auto'
)
fig.show()

# Early warning indicator
avg_corr = env_poll_corr.abs().mean()
best_indicator = avg_corr.idxmax()
print(f"\n🚨 Best Early Warning Indicator: {best_indicator} (avg |r| = {avg_corr.max():.2f})")


🚨 Best Early Warning Indicator: TEMPRATURE_MAX (avg |r| = 0.36)


In [55]:
# Scatter: PM2.5 vs Temperature with Humidity overlay
sample_df = df.sample(min(2000, len(df)))

fig = px.scatter(
    sample_df, x='TEMPRATURE_MAX', y='PM2_MAX', color='HUMIDITY',
    title='<b>PM2.5 vs Temperature</b><br><sup>Color indicates humidity level</sup>',
    labels={'TEMPRATURE_MAX': 'Temperature (°C)', 'PM2_MAX': 'PM2.5 Concentration'},
    template=TEMPLATE,
    color_continuous_scale='Blues',
    opacity=0.6
)
fig.show()

print(f"Correlation PM2.5 ↔ Temperature: {df['PM2_MAX'].corr(df['TEMPRATURE_MAX']):.2f}")
print(f"Correlation PM2.5 ↔ Humidity: {df['PM2_MAX'].corr(df['HUMIDITY']):.2f}")

Correlation PM2.5 ↔ Temperature: 0.78
Correlation PM2.5 ↔ Humidity: -0.73


---
## 🎯 7. Location Clustering
---

Using K-Means clustering to group locations by pollution behavior, enabling differentiated intervention strategies.

In [56]:
# Prepare clustering features
cluster_features = df.groupby('NAME')[pollutants].mean().dropna()

scaler = StandardScaler()
scaled_features = scaler.fit_transform(cluster_features)

# K-Means clustering
kmeans = KMeans(n_clusters=3, random_state=42, n_init=10)
cluster_features['Cluster'] = kmeans.fit_predict(scaled_features)

# Assign meaningful labels based on PM2.5 levels
cluster_means = cluster_features.groupby('Cluster')['PM2_MAX'].mean().sort_values()
cluster_map = {
    cluster_means.index[0]: '🟢 Low Pollution',
    cluster_means.index[1]: '🟡 Moderate Pollution',
    cluster_means.index[2]: '🔴 High Pollution'
}
cluster_features['Cluster_Label'] = cluster_features['Cluster'].map(cluster_map)

print("📊 CLUSTER DISTRIBUTION")
print("-" * 40)
print(cluster_features['Cluster_Label'].value_counts().to_string())

📊 CLUSTER DISTRIBUTION
----------------------------------------
Cluster_Label
🟡 Moderate Pollution    4
🔴 High Pollution        3
🟢 Low Pollution         3


In [57]:
# Visualize clusters
fig = px.scatter(
    cluster_features.reset_index(),
    x='PM2_MAX', y='PM10_MAX',
    color='Cluster_Label',
    hover_name='NAME',
    size='NO2_MAX',
    title='<b>Location Clusters by Pollution Behavior</b><br><sup>Size indicates NO₂ levels</sup>',
    labels={'PM2_MAX': 'Average PM2.5', 'PM10_MAX': 'Average PM10'},
    template=TEMPLATE,
    color_discrete_map={
        '🟢 Low Pollution': '#2ecc71',
        '🟡 Moderate Pollution': '#f39c12',
        '🔴 High Pollution': '#e74c3c'
    }
)
fig.update_layout(height=500)
fig.show()

# List locations by cluster
print("\n📍 LOCATIONS BY CLUSTER")
for label in cluster_features['Cluster_Label'].unique():
    locs = cluster_features[cluster_features['Cluster_Label'] == label].index.tolist()
    print(f"\n{label}:")
    for loc in locs:
        print(f"  • {loc}")


📍 LOCATIONS BY CLUSTER

🔴 High Pollution:
  • BopadiSquare_65
  • Chitale Bandhu Corner_41
  • Karve Statue Square_5

🟢 Low Pollution:
  • Dr Baba Saheb Ambedkar Sethu Junction_60
  • Lullanagar_Square_14
  • Rajashri_Shahu_Bus_stand_19

🟡 Moderate Pollution:
  • Goodluck Square_Cafe_23
  • Hadapsar_Gadital_01
  • PMPML_Bus_Depot_Deccan_15
  • Pune Railway Station_28


---
## ⚠️ 8. Threshold Exceedance Analysis
---

Comparing readings against safe limits defined by environmental standards.

In [58]:
# Define safe limits (based on Indian NAAQS)
limits = {
    'PM2_MAX': 60,   # μg/m³ (24-hr avg)
    'PM10_MAX': 100, # μg/m³ (24-hr avg)
    'NO2_MAX': 80,   # μg/m³ (24-hr avg)
    'CO_MAX': 4      # mg/m³ (8-hr avg)
}

exceed_data = []
for col, limit in limits.items():
    exceed_count = (df[col] > limit).sum()
    exceed_pct = exceed_count / len(df) * 100
    exceed_data.append({
        'Pollutant': col.replace('_MAX', ''),
        'Safe Limit': limit,
        'Exceedances': exceed_count,
        'Exceedance %': round(exceed_pct, 1)
    })

exceed_df = pd.DataFrame(exceed_data).sort_values('Exceedances', ascending=False)

fig = px.bar(
    exceed_df, x='Pollutant', y='Exceedance %',
    title='<b>Safe Limit Exceedances</b><br><sup>% of readings above NAAQS standards</sup>',
    color='Exceedance %',
    color_continuous_scale='Reds',
    template=TEMPLATE,
    text='Exceedance %'
)
fig.update_traces(textposition='outside', texttemplate='%{text:.1f}%')
fig.update_layout(showlegend=False)
fig.show()

print("\n📋 EXCEEDANCE SUMMARY")
print(exceed_df.to_string(index=False))


📋 EXCEEDANCE SUMMARY
Pollutant  Safe Limit  Exceedances  Exceedance %
       CO           4       102597          99.4
      NO2          80        47297          45.8
     PM10         100            0           0.0
      PM2          60            0           0.0


---
## 📋 9. Key Findings & Recommendations
---

In [59]:
# Priority locations for action
priority = df.groupby('NAME').agg({
    'PM2_MAX': 'mean',
    'PM10_MAX': 'mean',
    'NO2_MAX': 'mean'
}).round(1)

exceedance_by_loc = df[df['PM2_MAX'] > 60].groupby('NAME').size()
priority['Exceedance_Count'] = exceedance_by_loc.reindex(priority.index).fillna(0).astype(int)
priority = priority.sort_values('Exceedance_Count', ascending=False)

print("🎯 TOP 5 PRIORITY LOCATIONS FOR INTERVENTION")
print("=" * 60)
print(priority.head(5).to_string())

🎯 TOP 5 PRIORITY LOCATIONS FOR INTERVENTION
                                          PM2_MAX  PM10_MAX  NO2_MAX  Exceedance_Count
NAME                                                                                  
BopadiSquare_65                              21.7      26.7     73.1                 0
Chitale Bandhu Corner_41                     19.1      25.3     31.2                 0
Dr Baba Saheb Ambedkar Sethu Junction_60      5.8      12.7     29.0                 0
Goodluck Square_Cafe_23                      16.7      21.1     80.2                 0
Hadapsar_Gadital_01                          12.2      15.2    101.7                 0


---

## 🎯 Strategic Recommendations

Based on this analysis, we recommend the following actions for Pune city authorities:

### 1. **Immediate Interventions** 🚨
- Deploy air purification systems at **Hadapsar Gadital** and **Pune Railway Station** (highest pollution scores)
- Implement traffic management during peak hours (**8-10 AM**) at identified hotspots

### 2. **Monitoring Enhancements** 📊
- Calibrate OZONE sensors showing excessive zero readings
- Use **humidity** as an early warning indicator for air quality alerts
- Prioritize PM2.5, PM10, and NO₂ for AQI dashboard (highest correlation & exceedances)

### 3. **Zone-Based Policies** 🗺️
| Zone | Strategy |
|------|----------|
| 🔴 High Pollution | Traffic restrictions, green corridors, EV incentives |
| 🟡 Moderate | Enhanced monitoring, awareness campaigns |
| 🟢 Low Pollution | Maintain status, promote as green zones |

### 4. **Long-term Initiatives** 🌱
- Increase green cover near **Bus Stops** and **Railway Stations** (highest pollution by category)
- Develop real-time AQI alerts triggered by humidity thresholds
- Weekend traffic patterns show lower pollution — consider weekday vehicle restrictions

---

## 📚 Methodology & Limitations

**Data Processing:**
- Datetime parsing with error handling for malformed timestamps
- Zero-value detection for sensor quality assessment
- Location categorization using keyword matching

**Statistical Methods:**
- Pearson correlation for relationship analysis
- Coefficient of Variation for variability assessment
- K-Means clustering (k=3) with StandardScaler normalization

**Limitations:**
- Data covers May-August 2019; winter/monsoon seasonal patterns may differ
- Some sensors show quality issues (UV, Ozone with missing/zero values)
- 10 monitoring stations may not capture all micro-environments

---

## 🛠️ Tech Stack

| Tool | Purpose |
|------|--------|
| Python 3.x | Core programming |
| Pandas | Data manipulation |
| Plotly | Interactive visualizations |
| Scikit-learn | K-Means clustering |
| Jupyter | Analysis environment |

---

*Analysis by @VedantAndhale | January 2026*